### FRAP geometries

In [ ]:
from fem_sol import frap_solver
from matplotlib import cm, rc, rcParams
from matplotlib.ticker import MaxNLocator
import fem_utils
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import seaborn as sns
fol = '/Users/hubatsch/Desktop/DropletFRAP/Latex/Figures/'
sns.set_style("ticks")
rcParams['axes.linewidth'] = 0.75
rcParams['xtick.major.width'] = 0.75
rcParams['ytick.major.width'] = 0.75
rcParams['text.usetex']=True

In [ ]:
import pylab as pl
params = {'legend.fontsize': 9,
          'legend.handlelength': 1}
pl.rcParams.update(params)

def nice_fig(xla, yla, xli, yli, size, fs=12): 
    rc('font',**{'family':'sans-serif','sans-serif':['Helvetica']})
#     rc('font',**{'family':'serif','serif':['Palatino']})
    plt.gcf().set_size_inches(size[0], size[1])
    plt.xlabel(xla,fontsize=fs)  
    plt.ylabel(yla,fontsize=fs)
    plt.xlim(xli)
    plt.ylim(yli)
    plt.tick_params(axis='both', which='major', labelsize=fs)

def save_nice_fig(name):
    plt.savefig(name, format='pdf', dpi=300, bbox_inches='tight',
                transparent=True)

In [ ]:
me = ['Meshes/multi_drop_gauss.xml', 'Meshes/multi_drop_gauss_med.xml',
     'Meshes/multi_drop_gauss_far.xml', 'Meshes/multi_drop_gauss.xml',
     'Meshes/multi_drop_gauss_med.xml', 'Meshes/multi_drop_gauss_far.xml']
point_lists = [[[4, 4.5, 0.5], [4, 3.5, 0.5], [3.5, 4, 0.5], [4.5, 4, 0.5]],
               [[4, 5, 0.5], [4, 3, 0.5], [3, 4, 0.5], [5, 4, 0.5]],
               [[4, 5.5, 0.5], [4, 2.5, 0.5], [2.5, 4, 0.5], [5.5, 4, 0.5]],
               [[4, 4.5, 0.5], [4, 3.5, 0.5], [3.5, 4, 0.5], [4.5, 4, 0.5]],
               [[4, 5, 0.5], [4, 3, 0.5], [3, 4, 0.5], [5, 4, 0.5]],
               [[4, 5.5, 0.5], [4, 2.5, 0.5], [2.5, 4, 0.5], [5.5, 4, 0.5]]]
phi_tot_int = [.99, .99, .99, .9, .9, .9]
phi_tot_ext = [.01, .01, .01, .1, .1, .1]
G_in = [1, 1, 1, .1, .1, .1]
G_out = [1, 1, 1, 0.99/0.9, 0.99/0.9, 0.99/0.9]

f_i = []

for p, m, p_i, p_e, G_i, G_o in zip(point_lists, me, phi_tot_int,
                                    phi_tot_ext, G_in, G_out):
    f = frap_solver([4, 4, 0.5], m, name='FRAP_multi_'+m[:-4]+str(G_i), point_list=p,
                    T=50, phi_tot_int=p_i, phi_tot_ext=p_e, G_in=G_i, G_out=G_o)
    f.solve_frap()
    f_i.append(f)

In [ ]:
alphas = np.linspace(0,2*np.pi, 20)
ns = np.c_[np.cos(alphas), np.sin(alphas), np.zeros(len(alphas))]
eps = np.linspace(0, 0.23, 100)
profs = []
for i in range(len(f_i)):
#     if i>2:
        profs.append([])
        for j in range(50):
            values=[]
            fs = fem_utils.load_time_point(f_i[i].name+'t_p_'+str(j)+'.h5',
                                           f_i[i].mesh)
            for n in ns:
                values.append([fs([4, 4, 0.5]+e*n) for e in eps])
            profs[i].append(np.mean(np.transpose(values), 1))

In [ ]:
np.savetxt('t_p.csv', profs, delimiter=',')

In [ ]:
ft = f_i[1]
meta_data = np.r_[ft.dt, ft.T, eps]
np.savetxt('meta_data.csv', meta_data, delimiter=',')

In [ ]:
plt.plot(eps,np.transpose(profs)[:,:])

In [ ]:
nice_fig('t [s]', 'intensity (a.u)', [0,50], [0,1.1], [1.5,2])
plt.plot([np.mean(x)/f_i[0].phi_tot_int for x in profs[0]],
         lw=2, label='d=0.5', ls='-')
plt.plot([np.mean(x)/f_i[1].phi_tot_int for x in profs[1]],
         lw=2, label='d=1', ls='--')
plt.plot([np.mean(x)/f_i[2].phi_tot_int for x in profs[2]],
         lw=2, label='d=1.5', ls=':')
plt.plot(range(0, 100), np.ones(100), linestyle='--', color='k')
plt.title('$\Phi_{out}=0.01}$', size=12)
plt.gca().get_yaxis().set_visible(False)
save_nice_fig(fol+'Fig3/tot_recov_neighbours_bad.pdf')

In [ ]:
nice_fig('t [s]', 'intensity (a.u)', [0,30], [0,1.1], [1.5,2])
plt.plot([np.mean(x)/f_i[3].phi_tot_int for x in profs[3]],
         lw=2, label='d=0.5', ls='-')
plt.plot([np.mean(x)/f_i[4].phi_tot_int for x in profs[4]],
         lw=2, label='d=1', ls='--')
plt.plot([np.mean(x)/f_i[5].phi_tot_int for x in profs[5]],
         lw=2, label='d=1.5', ls=':')
plt.plot(range(0, 100), np.ones(100), linestyle='--', color='k')
plt.title('$\Phi_{out}=0.1}$', size=12)
plt.legend(prop={'size': 9}, frameon=False)
save_nice_fig(fol+'Fig3/tot_recov_neighbours_good.pdf')

In [ ]:
nice_fig('x [$\mu m$]', 'intensity (a.u)', [0,0.25], [0,1.1], [3.8,2])
l_sim = plt.plot(eps, np.transpose(profs[0])[:,::8]/f_i[0].phi_tot_int, '#1f77b4', lw=2.5)
plt.plot(range(0, 100), np.ones(100), linestyle='--', color='k')
l_fit = plt.plot(np.linspace(0, 0.23, 100), np.transpose(ml)[:,::8],
                 ls='--', c='orange', lw=1.5)
plt.legend([l_sim[0], l_fit[0]], ['Simulation', 'Fit'], prop={'size': 9}, frameon=False)
save_nice_fig(fol+'Fig3/spat_recov_neighbours.pdf')

In [ ]:
# Define parameters for all simulations
point_list = [[4, 4, 0.5], [4, 4, 1.5], [4, 4, 4],
              [4, 4, 0.5], [4, 4, 1.5], [4, 4, 4]]
me = ['coverslip.xml', '1_5.xml', 'symmetric.xml',
      'coverslip.xml', '1_5.xml', 'symmetric.xml']
phi_tot_int = [.99, .99, .99, .9, .9, .9]
phi_tot_ext = [.01, .01, .01, .1, .1, .1]
G_in = [1, 1, 1, .1, .1, .1]
G_out = [1, 1, 1, 0.99/0.9, 0.99/0.9, 0.99/0.9]
f_cs = []

# Zip all parameters, iterate
for p, m, p_i, p_e, G_i, G_o in zip(point_list, me, phi_tot_int,
                                   phi_tot_ext, G_in, G_out):
    f_cs.append(frap_solver(p, 'Meshes/single_drop_'+m,
                name='FRAP_'+m[:-4]+str(G_i), T=60, phi_tot_int=p_i,
                phi_tot_ext=p_e, G_in=G_i, G_out=G_o))
    f_cs[-1].solve_frap()

In [ ]:
z = [0.5, 1.5, 4, 0.5, 1.5, 4]
profs_cs = []
for i, z_i in enumerate(z):
    profs_cs.append([])
    for j in range(50):
        values=[]
        fs = fem_utils.load_time_point(f_cs[i].name+'t_p_'+str(j)+'.h5',
                                       f_cs[i].mesh)
        for n in ns:
            values.append([fs([4, 4, z_i]+e*n) for e in eps])
        profs_cs[i].append(np.mean(np.transpose(values), 1))

In [ ]:
np.savetxt('t_p_neighbours.csv', profs_cs[0], delimiter=',')

In [ ]:
nice_fig('t [s]', '', [0,50], [0,1.1], [1.5,2])
ls = ['-', '--', ':']
for i, f in enumerate(f_cs[0:3]):
    plt.plot([np.mean(x)/f.phi_tot_int for x in profs_cs[i]],
             label='d='+str(z[i]), ls=ls[i], lw=2)
plt.plot(range(0, 100), np.ones(100), linestyle='--', color='k')
plt.title('$\Phi_{out}=0.01}$', size=12)
plt.gca().get_yaxis().set_visible(False)
save_nice_fig(fol+'Fig3/tot_recov_cs_bad.pdf')

In [ ]:
nice_fig('t [s]', 'intensity (a.u)', [0,30], [0,1.1], [1.5,2])
ls = ['-', '--', ':']
for i, f in enumerate(f_cs[3:]):
    plt.plot([np.mean(x)/f.phi_tot_int for x in profs_cs[i+3]],
             label='h='+str(z[i]), lw=2, ls=ls[i])
plt.plot(range(0, 100), np.ones(100), linestyle='--', color='k')
plt.title('$\Phi_{out}=0.1}$', size=12)
plt.legend(prop={'size': 9}, frameon=False)
save_nice_fig(fol+'Fig3/tot_recov_cs_good.pdf')

In [ ]:
ml_neigh = np.loadtxt('/Users/hubatsch/Desktop/DropletFRAP/matlab_fit_neigh.csv',
                      delimiter=',')
nice_fig('x [$\mu m$]', 'intensity (a.u)', [0,0.25], [0,1.1], [3.8,2])
l_sim = plt.plot(eps, np.transpose(profs_cs[0])[:,::8]/f_cs[0].phi_tot_int, '#1f77b4',
                 lw=2.5, label='Simulation')
plt.plot(range(0, 100), np.ones(100), linestyle='--', color='k')
l_fit = plt.plot(np.linspace(0, 0.23, 100), np.transpose(ml_neigh)[:,::8],
         ls='--', c='orange', lw=1.5)
plt.legend([l_sim[0], l_fit[0]], ['Simulation', 'Fit'], frameon=False)
save_nice_fig(fol+'Fig3/spat_recov_coverslip.pdf')

### Figure 1: Fitting $D_{in}$ and data analysis.

**Panel: comparison PGL-3 diffusivity with Louise's viscosity**

In [ ]:
louise = pd.read_csv('/Users/hubatsch/Desktop/DropletFRAP/Latex/Figures/Fig1/Louise.csv')
lars = pd.read_csv('/Users/hubatsch/Desktop/DropletFRAP/Latex/Figures/Fig1/Lars.csv')

In [ ]:
fig, ax1 = plt.subplots()
ax2 = ax1.twinx()
plt.sca(ax1)
sns.lineplot(x="conc", y="D", data=lars, color=sns.color_palette()[1])
sns.scatterplot(x="conc", y="D", data=lars, color=sns.color_palette()[1], alpha=0.7)
plt.xlabel('$c_{salt}\; [mM]$')
plt.ylabel('$D_{in} \;[\mu m^2\cdot s^{-1}]$', color=sns.color_palette()[1])
plt.yticks([0, 0.05, 0.1], rotation=90, color = sns.color_palette()[1])
plt.ylim(0, 0.1)
ax1.set_zorder(1) 
ax1.patch.set_visible(False)
plt.sca(ax2)
sns.lineplot(x="conc", y="vis", data=louise, color=sns.color_palette()[0], label='data from ref[xxx]')
nice_fig('c_{salt} [mM]', '$\eta^{-1} \;[Pa\cdot s]^{-1}$', [40,190], [0,7.24], [2.3,2])
plt.yticks(color = sns.color_palette()[0])
plt.ylabel('$\eta^{-1} \;[Pa\cdot s]^{-1}$ ', color = sns.color_palette()[0])
plt.legend(frameon=False, fontsize=9)
save_nice_fig(fol+'Fig1/Lars_vs_Louise.pdf')

**Panel:coacervates PLYS/ATP, CMD/PLYS**m

In [ ]:
coacervates = pd.read_csv('/Users/hubatsch/Desktop/DropletFRAP/Latex/Figures/Fig1/Coacervates.csv')
sns.stripplot(data=coacervates, jitter=0.35, alpha=0.8,**{'marker': '.', 'size': 8, 'edgecolor': 'black', 'color': 'k'})
ax = sns.barplot(data=coacervates, facecolor=(1, 1, 1, 0), edgecolor=(0.6, 0.6, 0.6), errcolor=(0.6, 0.6, 0.6), capsize=.2, ci='sd', errwidth=1.5)
plt.setp(ax.lines, zorder=100)
nice_fig(None, '$D_{in} \;[\mu m^2\cdot s^{-1}]$', [None, None], [0,6], [2.3,2])
plt.xticks([0,1], ('CMD/PLYS', 'PLYS/ATP'), rotation=20)
plt.xlim(-0.7, 1.7)
save_nice_fig(fol+'Fig1/Coacervates.pdf')

In [ ]:
ax.patches

**Panel: time course CMD**

In [ ]:
CMD = np.loadtxt(fol+'/Fig1/CMD_timecourse.csv', delimiter=',')
CMD_fit = np.loadtxt(fol+'/Fig1/CMD_fit_timecourse.csv', delimiter=',')
l_sim = plt.plot(CMD[:, 0], CMD[:, 1:], '#1f77b4', lw=3, label='Simulation')
l_fit = plt.plot(CMD_fit[:, 0], CMD_fit[:, 1:], '--', lw=2, c=sns.color_palette()[1], label='Simulation')
plt.plot(range(0, 10), np.ones(10)*np.min(CMD_fit[:, 1]), linestyle='--', color='k', lw=2)
nice_fig('x [$\mu m$]', 'intensity (a.u)', [0,np.max(CMD_fit[:, 0])], [0,0.6], [2.3,2])
save_nice_fig(fol+'Fig1/CMD_spat_recov.pdf')

**Panel: time course PGL-3**

In [ ]:
PGL = np.loadtxt(fol+'/Fig1/PGL_timecourse.csv', delimiter=',')
PGL_fit = np.loadtxt(fol+'/Fig1/PGL_fit_timecourse.csv', delimiter=',')
l_sim = plt.plot(PGL[:, 0], PGL[:, 1:], '#1f77b4', lw=3, label='Simulation')
l_fit = plt.plot(PGL_fit[:, 0], PGL_fit[:, 1:], '--', lw=2, c=sns.color_palette()[1], label='Simulation')
plt.plot(range(0, 10), np.ones(10)*np.min(PGL_fit[:, 1]), linestyle='--', color='k', lw=2)
nice_fig('x [$\mu m$]', 'intensity (a.u)', [0,np.max(PGL_fit[:, 0])], [0,None], [2.3,2])
save_nice_fig(fol+'Fig1/PGL_spat_recov.pdf')

**Panel: time course total intensity**

In [ ]:
PGL = np.loadtxt(fol+'/Fig1/PGL_tot.csv', delimiter=',')
ATP = np.loadtxt(fol+'/Fig1/ATP_tot.csv', delimiter=',')
CMD = np.loadtxt(fol+'/Fig1/CMD_tot.csv', delimiter=',')
# fig, ax1 = plt.subplots()
# ax2 = ax1.twiny()
# plt.sca(ax1)
nice_fig('$t/T_{max}$', 'intensity (a.u)', [0,200], [0,0.62], [2.3,2])
# plt.sca(ax2)
# ax2.tick_params(axis="x",direction="in")
plt.plot(PGL[::10, 0]/np.max(PGL[1:-1:2, 0]), PGL[::10,1], label='PGL-3', c='#CC406E', markersize=3, alpha=0.7, lw=2)
plt.plot(ATP[::1, 0]/np.max(ATP[:, 0]), ATP[::1,1], label='PLYS/ATP', c='#FF508A', markersize=3, alpha=0.7, lw=2)
plt.plot(CMD[::5, 0]/np.max(CMD[:, 0]), CMD[::5,1], label='CMD/PLYS', c='#7F2845', markersize=3, alpha=0.7, lw=2)
plt.legend(frameon=False, fontsize=9)
plt.xlim(0, 1)
save_nice_fig(fol+'Fig1/tot_recov.pdf')

### Figure 4: Obtaining info about outside: experiments.

**Panel: data time course with full model.**

In [ ]:
PLYS = np.loadtxt(fol+'Fig4/PLYS_timecourse.csv', delimiter=',')
PLYS_fit = np.loadtxt(fol+'Fig4/PLYS_fit_timecourse.csv', delimiter=',')
l_data = plt.plot(PLYS[:, 0], PLYS[:, 1:], '#1f77b4', lw=3,
                  label='Experiment')
l_fit = plt.plot(PLYS_fit[:, 0], PLYS_fit[:, 1:], '--', lw=2,
                 c=sns.color_palette()[1], label='Simulation')
nice_fig('x [$\mu m$]', 'intensity (a.u)', [0, 2.4*np.max(PLYS[:, 0])],
         [0,0.5], [2.3,2])
plt.legend([l_data[0], l_fit[0]], ['ATP/PLYS', 'Full model'], frameon=False,
           fontsize=9, handletextpad=0.4, handlelength=0.8)
save_nice_fig(fol+'Fig4/PLYS_spat_recov.pdf')

**Panel: Experimental Partitioning vs $D_{out}$ for CMD**

In [ ]:
PLYS = pd.read_csv('/Users/hubatsch/Desktop/DropletFRAP/Latex/Figures/Fig4/PLYS.csv')
CMD = pd.read_csv('/Users/hubatsch/Desktop/DropletFRAP/Latex/Figures/Fig4/CMD.csv')

In [ ]:
fig, ax1 = plt.subplots()
plt.sca(ax1)
sns.lineplot(x="P", y="D_out", data=CMD, color=sns.color_palette()[1], ci='sd')
sns.lineplot(x="P", y="D_out", data=PLYS, color=sns.color_palette()[2], ci='sd')
plt.plot(np.logspace(0, 2, 10), 2*np.logspace(0, 2, 10), '--', c='grey')
ax1.set_yscale('log')
ax1.set_xscale('log')
nice_fig('Partitioning P', '$D_{out} \;[\mu m^2s^{-1}]$', [1,100], [0.1,100], [2.3,2])
plt.legend(['CMD/PLYS', 'PLYS/ATP'], frameon=False, fontsize=9)
plt.xticks([1, 10, 100]);
save_nice_fig(fol+'Fig4/PLYS_CMD.pdf')

**Panel: Experimental Partitioning vs $D_out$ for PGL-3**

In [ ]:
PGL_50 = pd.read_csv('/Users/hubatsch/Desktop/DropletFRAP/Latex/Figures/Fig4/PGL_50.csv')
PGL_60 = pd.read_csv('/Users/hubatsch/Desktop/DropletFRAP/Latex/Figures/Fig4/PGL_60.csv')
PGL_75 = pd.read_csv('/Users/hubatsch/Desktop/DropletFRAP/Latex/Figures/Fig4/PGL_75.csv')
PGL_90 = pd.read_csv('/Users/hubatsch/Desktop/DropletFRAP/Latex/Figures/Fig4/PGL_90.csv')
PGL_100 = pd.read_csv('/Users/hubatsch/Desktop/DropletFRAP/Latex/Figures/Fig4/PGL_100.csv')
PGL_120 = pd.read_csv('/Users/hubatsch/Desktop/DropletFRAP/Latex/Figures/Fig4/PGL_120.csv')
PGL_150 = pd.read_csv('/Users/hubatsch/Desktop/DropletFRAP/Latex/Figures/Fig4/PGL_150.csv')
PGL_180 = pd.read_csv('/Users/hubatsch/Desktop/DropletFRAP/Latex/Figures/Fig4/PGL_180.csv')

In [ ]:
fig, ax1 = plt.subplots()
plt.sca(ax1)
sns.set_palette(sns.color_palette("Oranges", 9))
# sns.color_palette("flare", as_cmap=True)
l50 = sns.lineplot(x="P", y="D_out", data=PGL_50, color=sns.color_palette()[1], ci=None)
l60 = sns.lineplot(x="P", y="D_out", data=PGL_60, color=sns.color_palette()[2], ci=None)
l75 = sns.lineplot(x="P", y="D_out", data=PGL_75, color=sns.color_palette()[3], ci=None)
l90 = sns.lineplot(x="P", y="D_out", data=PGL_90, color=sns.color_palette()[4], ci=None)
leg1 = plt.legend(['50 mM', '60 mM', '75 mM', '90 mM'], labelspacing=0.3,
           loc=(0.65, 0.0), handletextpad=0.4, handlelength=0.5, frameon=0)
l100 = sns.lineplot(x="P", y="D_out", data=PGL_100, color=sns.color_palette()[5], ci=None)
l120 = sns.lineplot(x="P", y="D_out", data=PGL_120, color=sns.color_palette()[6], ci=None)
l150 = sns.lineplot(x="P", y="D_out", data=PGL_150, color=sns.color_palette()[7], ci=None)
l180 = sns.lineplot(x="P", y="D_out", data=PGL_180, color=sns.color_palette()[8], ci=None)
plt.plot(np.logspace(0, 3, 10), 0.07*np.logspace(0, 3, 10), '--', c='grey')
ax1.set_yscale('log')
ax1.set_xscale('log')
nice_fig('Partitioning P', '$D_{out} \;[\mu m^2 s^{-1}]$', [1,1000], [0.0003,200], [2.3,2])
plt.xticks([1, 10, 100, 1000]);
plt.legend(loc=1)
plt.legend(['50 mM', '60 mM', '75 mM', '90 mM', '100 mM', '120 mM', '150 mM', '180 mM'], labelspacing=0.3,
           loc=(0, 0.56), handletextpad=0.4, handlelength=0.5, frameon=0)
plt.gca().add_artist(leg1)
save_nice_fig(fol+'Fig4/PGL-3.pdf')

### Figure 5: Obtaining info about outside: theory.

**Panel: Partitioning vs. $D_{out}$, showcasing four different simulation start cases.**

In [ ]:
P_Do = np.loadtxt(fol+'/Fig4/Part_vs_Do.csv', delimiter=',')
P = [5, 150, 5, 150]
D_o = [0.1, 0.1, 1, 1]
plt.gca().set_prop_cycle(None)
nice_fig('Partitioning P', '$D_{out}$ [$\mu m^2/s$]', [0.9,320], [0.000001,340], [2.3,2])
lines = plt.loglog(P_Do[0, :], P_Do[1:, :].transpose())
plt.plot(P_Do[0, :], P_Do[0, :], '--', c='grey')
plt.legend([lines[2], lines[0], lines[3], lines[1]],
           ['0.2', '0.02', '0.0067', '0.00067'], ncol=2, frameon=False,
               title=r'\underline{$D_{out}$/P [$\mu m^2/s$]:}', columnspacing=0.5, labelspacing=0.3,
           loc=(0.4, 0), handletextpad=0.4, handlelength=0.5)
plt.gca().set_prop_cycle(None)
plt.plot(P[0], D_o[0], 'd')
plt.plot(P[1], D_o[1], 'd')
plt.plot(P[2], D_o[2], 'd')
plt.plot(P[3], D_o[3], 'd')
plt.annotate('$D_{out}$/P = 1 $\mu m^2/s$', [1,40], c='grey')
plt.xticks([1, 10, 100]);
save_nice_fig(fol+'Fig4/D_vs_P.pdf')

**Panel: Cost function**

In [ ]:
P_Cost = np.loadtxt(fol+'/Fig4/Part_vs_Cost.csv', delimiter=',')
nice_fig('Partitioning P', 'Cost function [a.u.]', [0.9,320], [0.000000001,0.01], [2.3,2])
lines = plt.loglog(P_Cost[0, :], P_Cost[1:, :].transpose())
plt.legend([lines[2], lines[0], lines[3], lines[1]],
           ['0.2', '0.02', '0.0067', '0.00067'], ncol=2, frameon=False,
           title=r'\underline{$D_{out}$/P set to:}', columnspacing=0.5, labelspacing=0.3,
           loc=(0.081, 0), handletextpad=0.4, handlelength=0.5)
plt.xticks([1, 10, 100]);
save_nice_fig(fol+'Fig4/D_vs_Cost.pdf')

**Panel: Valley in parameter space**

In [ ]:
con = np.loadtxt(fol+'Fig4/Valley.csv', delimiter=',')
levels = MaxNLocator(nbins=15).tick_values(np.log10(con[:, 2:].min()), np.log10(con[:, 2:].max()))
nice_fig('Partitioning P', '$D_{out} \;[\mu m^2 s^{-1}]$', [1, 3], [-2,1], [2.3,2])
CS = plt.contourf(np.log10(con[:, 0]), np.log10(con[:, 1]), np.log10(con[:, 2:]), levels=levels, cmap=cm.coolwarm)
plt.plot(np.log10(150), np.log10(10**-1), 'y*', label='Initial Simul.', markersize=3)
plt.legend(loc=(0, 0.83), frameon=False, handletextpad=0.4)
plt.xticks([1, 2, 3], ['$10^1$', '$10^2$', '$10^3$'])
plt.yticks([-2, -1, 0, 1], ['$10^{-2}$', '$10^{-1}$', '$10^0$', '$10^1$'])
plt.tick_params('x', pad=5)
fig1 = plt.gcf()
clb = fig1.colorbar(CS, ticks=[0, -2, -4, -6])
clb.ax.set_title('Cost')
save_nice_fig(fol+'Fig4/Sim_D_out_P.pdf')

**Panel: Zoom in for valley in parameter space**

In [ ]:
levels = MaxNLocator(nbins=15).tick_values(np.log10(con[:, 2:].min()), np.log10(con[:, 2:].max()))
nice_fig('Partitioning P', '', [1.9, 2.4], [-1.5,-0.5], [2.3,2])
CS = plt.contourf(np.log10(con[16:-27, 0]), np.log10(con[16:-27, 1]),
                  np.log10(con[16:-27, 2+16:-27]), levels=levels,
                  cmap=cm.coolwarm, vmax=-1.5)
plt.plot(np.log10(150), np.log10(10**-1), 'y*', label='Initial Simul.', markersize=3)
plt.legend(loc=(0, 0.83), frameon=False, handletextpad=0.4)
plt.xticks([2, 2.25], ['$10^2$', '$10^{2.25}$'])
plt.yticks([-1.5, -1, -0.5], ['$10^{-1.5}$', '$10^{-1}$', '$10^{-0.5}$'])
plt.tick_params('x', pad=5)
fig1 = plt.gcf()
clb = fig1.colorbar(CS, ticks=[-2, -4, -6])
clb.ax.set_title('Cost')
save_nice_fig(fol+'Fig4/Sim_D_out_P_inset.pdf')